# butcher5

The Markov Butcher Shop sells two types of meat: beef and pork. Customers arrive at the butcher shop and form a single queue. There are two butchers who serve customers from the queue on a first-come-first-served basis.

Customer demand is as follows: beef only, 50%; pork only, 30%; both beef and pork, 20%. Customers who want only one type of meat place 1 order; those who want both types of meat must place 2 separate orders.

Based on historical data, the interarrival time between customers is uniformly distributed between 1.5 and 3.5 minutes. The time for a butcher to fill a single order is uniformly distributed between 2.5 and 6.5 minutes. The interarrival times and service times are assumed to be independent.

Simulate the shop for 2 hours. The butcher shop is interested in the following performance measures:

* the average time a customer spends in the queue (i.e. average delay),
* the time average number of customers in the queue,
* the time average number of busy butchers.

Determine a point estimate (i.e. observed sample mean) and an interval estimate (i.e. 95% confidence interval) for each performance measure using 50 replications.

#### Setup

In [1]:
##### Setup #####
# Import everything from SimPy
from SimPy.Simulation import *

# Import bisect_left from bisect
from bisect import bisect_left

# Import various functions from NumPy
from numpy import mean, std, sqrt, inf

# Import seed initializer and random sampling functions from NumPy
from numpy.random import seed, rand, uniform

# Import t random variable from SciPy
from scipy.stats import t

#### Model

Below is the SimPy code from the **butcher4** homework problem, with the appropriate modifications.

In [2]:
##### Distributions #####
class D:
    # Customer type distribution: 
    # Beef = 0, Pork = 1, Both = 2
    def customerType():
        # Sorted list of values that X can take, including -inf
        a = [-inf, 0, 1, 2]

        # cdf at each value that X can take
        cdf = [0, 0.50, 0.80, 1]

        # Generate variate
        variate = a[bisect_left(cdf, rand())]

        # Return generated variate
        return variate
    

##### Parameters #####
class P:
    # Customers arrive at the entrance with uniformly distributed
    # interarrival times between 1.5 and 3.5 minutes
    interarrivalTimeMin = 1.5
    interarrivalTimeMax = 3.5
    
    # Service times are uniformly distributed between 2.5 and 6.5 minutes
    serviceTimeMin = 2.5
    serviceTimeMax = 6.5
    
    # Number of servers
    nServers = 2
    
    # Shop is open for 2 continuous hours
    simulationTimeMax =  2 * 60
    

##### Processes #####
# Beef only customer
class CustomerBeef(Process):
    def behavior(self):
        # Customer arrives, joins queue
        arrivalTime = now()
        yield request, self, R.server
        
        # Customer is released from queue and starts service
        M.delay.observe(now() - arrivalTime)
        serviceTime = uniform(low = P.serviceTimeMin, high = P.serviceTimeMax)
        yield hold, self, serviceTime
        
        # Customer finishes service, leaves
        yield release, self, R.server
        
# Pork only customer
class CustomerPork(Process):
    def behavior(self):
        # Customer arrives, joins queue
        arrivalTime = now()
        yield request, self, R.server
        
        # Customer is released from queue and starts service
        M.delay.observe(now() - arrivalTime)
        serviceTime = uniform(low = P.serviceTimeMin, high = P.serviceTimeMax)
        yield hold, self, serviceTime
        
        # Customer finishes service, leaves
        yield release, self, R.server

# Beef and pork customer
class CustomerBoth(Process):
    def behavior(self):
        # Customer arrives, joins queue
        arrivalTime = now()
        yield request, self, R.server
        
        # Customer is released from queue and starts service
        M.delay.observe(now() - arrivalTime)
        serviceTime1 = uniform(low = P.serviceTimeMin, high = P.serviceTimeMax)
        serviceTime2 = uniform(low = P.serviceTimeMin, high = P.serviceTimeMax)
        yield hold, self, serviceTime1 + serviceTime2
        
        # Customer finishes service, leaves
        yield release, self, R.server
    
# Entrance
class Entrance(Process):
    def behavior(self):
        # At the start of the simulation, no customers have arrived
        nCustomers = 0
        
        # Customer arrivals
        while True:
            # Wait until the next arrival
            interarrivalTime = uniform(low = P.interarrivalTimeMin, high = P.interarrivalTimeMax)
            yield hold, self, interarrivalTime
            
            # Customer type?
            customerType = D.customerType()
            
            # Create a new customer, depending on this passenger's type
            if customerType == 0:
                c = CustomerBeef(name="Customer {0} (Beef)".format(nCustomers))
            elif customerType == 1:
                c = CustomerPork(name="Customer {0} (Pork)".format(nCustomers))
            elif customerType == 2:
                c = CustomerBoth(name="Customer {0} (Both)".format(nCustomers))

            # Count this new passenger
            nCustomers += 1
            
            # Activate the customer's behavior
            activate(c, c.behavior())

            # Count this new customer
            nCustomers += 1


##### Resources #####
class R:
    # Server
    server = None
    

##### Monitors #####
class M:
    # Queue waiting time
    delay = None
    

##### Simulation #####
def model(inputSeed):
    # Initialize SimPy 
    initialize()

    # Initialize a seed for the random number generator (more on this later in the semester)
    seed(inputSeed)

    # Create the server resource
    R.server = Resource(capacity=P.nServers, monitored=True)
    
    # Create the delay monitor
    M.delay = Monitor()

    # Activate the entrance (to generate customers)
    e = Entrance()
    activate(e, e.behavior())
    
    # Run the simulation
    simulate(until=P.simulationTimeMax)
    
    # Compute average delay
    avgDelay = M.delay.mean()
    
    # Compute time average number of customers in queue
    tAvgCustQ = R.server.waitMon.timeAverage()
    
    # Compute time average number of busy butchers
    tAvgBusyS = R.server.actMon.timeAverage()
    
    # Return a list of performance measures
    return [avgDelay, tAvgCustQ, tAvgBusyS]

#### Experiment

In [3]:
# Replicate simulation 50 times
# Create a list of observations for each performance measure
n = 50
avgDelayObs = []
tAvgCustQObs = []
tAvgBusySObs = []
for i in range(n):
    [avgDelay, tAvgCustQ, tAvgBusyS] = model(i*123)
    avgDelayObs.append(avgDelay)
    tAvgCustQObs.append(tAvgCustQ)
    tAvgBusySObs.append(tAvgBusyS)

    
#### Average delay ####
# Observed sample mean
avgDelaySM = mean(avgDelayObs)

# Observed sample standard deviation
avgDelaySSD = std(avgDelayObs, ddof = 1)

# Confidence level 0.05
alpha = 0.05
avgDelayCIL = avgDelaySM - t.ppf(1 - alpha/2, n - 1) * avgDelaySSD / sqrt(n)
avgDelayCIR = avgDelaySM + t.ppf(1 - alpha/2, n - 1) * avgDelaySSD / sqrt(n)

print("Average delay:")
print("  Sample mean: {0}".format(avgDelaySM))
print("  Sample standard deviation: {0}".format(avgDelaySSD))
print("  {0}% confidence interval: [{1}, {2}]".format((1 - alpha)*100, avgDelayCIL, avgDelayCIR))


#### Time average number of customers in queue ####
# Observed sample mean
tAvgCustQSM = mean(tAvgCustQObs)

# Observed sample standard deviation
tAvgCustQSSD = std(tAvgCustQObs, ddof = 1)

# Confidence level 0.05
alpha = 0.05
tAvgCustQCIL = tAvgCustQSM - t.ppf(1 - alpha/2, n - 1) * tAvgCustQSSD / sqrt(n)
tAvgCustQCIR = tAvgCustQSM + t.ppf(1 - alpha/2, n - 1) * tAvgCustQSSD / sqrt(n)

print("Time average number of customers in queue:")
print("  Sample mean: {0}".format(tAvgCustQSM))
print("  Sample standard deviation: {0}".format(tAvgCustQSSD))
print("  {0}% confidence interval: [{1}, {2}]".format((1 - alpha)*100, tAvgCustQCIL, tAvgCustQCIR))


#### Time average number of busy servers ####
# Observed sample mean
tAvgBusySSM = mean(tAvgBusySObs)

# Observed sample standard deviation
tAvgBusySSSD = std(tAvgBusySObs, ddof = 1)

# Confidence level 0.05
alpha = 0.05
tAvgBusySCIL = tAvgBusySSM - t.ppf(1 - alpha/2, n - 1) * tAvgBusySSSD / sqrt(n)
tAvgBusySCIR = tAvgBusySSM + t.ppf(1 - alpha/2, n - 1) * tAvgBusySSSD / sqrt(n)

print("Time average number of busy servers:")
print("  Sample mean: {0}".format(tAvgBusySSM))
print("  Sample standard deviation: {0}".format(tAvgBusySSSD))
print("  {0}% confidence interval: [{1}, {2}]".format((1 - alpha)*100, tAvgBusySCIL, tAvgBusySCIR))

Average delay:
  Sample mean: 5.4235650031831755
  Sample standard deviation: 2.921001395569028
  95.0% confidence interval: [4.593425592754395, 6.253704413611956]
Time average number of customers in queue:
  Sample mean: 2.184485766046792
  Sample standard deviation: 1.1586482415242176
  95.0% confidence interval: [1.8552015796125412, 2.5137699524810424]
Time average number of busy servers:
  Sample mean: 1.900141298427271
  Sample standard deviation: 0.049862196651239435
  95.0% confidence interval: [1.8859706189494954, 1.9143119779050466]
